In [9]:
import gc
gc.collect()

0

In [93]:
import warnings
warnings.filterwarnings('ignore')

In [12]:
import os
import pandas as pd
import json
from tqdm.auto import tqdm
# Specify the path to the folder containing the JSON files
folder_path = r'D:\Xelp_work\FSL Project\Sprint_2\HCFA_data\donut_data\valid\key'

# Initialize an empty DataFrame
master_df = pd.DataFrame()

# Function to split and expand rows based on the Value column
master_df = pd.DataFrame()

# Function to split and expand rows based on the Value column
def split_and_expand(row):
    keys = [row['KeyName']] * len(row['Value'].split(';'))
    values = row['Value'].split(';')
    filenames = [row['FileName']] * len(values)  # Ensure FileName is carried over
    return pd.DataFrame({'FileName': filenames, 'KeyName': keys, 'Value': values})

# Iterate through all the JSON files in the folder
# for filename in tqdm(os.listdir(folder_path)):
#     if filename.endswith('.json'):
#         file_path = os.path.join(folder_path, filename)
        
#         # Read the JSON file
#         with open(file_path, 'r') as file:
#             data = json.load(file)
#         # Convert the JSON data into a DataFrame with columns FileName, KeyName, and Value
#         rows = []
#         for key, value in data.items():
#             rows.append({'FileName': os.path.splitext(filename)[0], 'KeyName': key, 'Value': value})
#         df = pd.DataFrame(rows)
#         # Apply split_and_expand to each row and combine the results
#         expanded_df = df.apply(lambda row: split_and_expand(row), axis=1)
#         # Concatenate the expanded dataframes into one DataFrame
#         expanded_df = pd.concat(expanded_df.values, ignore_index=True)
#         # Append the DataFrame to the master DataFrame
#         master_df = pd.concat([master_df, expanded_df], ignore_index=True)

  0%|          | 0/6981 [00:00<?, ?it/s]

In [20]:
master_df['FileName'] = master_df['FileName'].apply(lambda x: f"{x}.tiff")

In [21]:
master_df['FileName'].nunique()

6981

In [22]:
master_df['FileName'][0]

'BSC134A9O003_000_HCFA.tiff'

In [76]:
# master_df.to_parquet(r"D:\Xelp_work\FSL Project\Sprint_2\HCFA_Results\Ground_truth_from_Json.parquet", index=False)

In [94]:
master_df = pd.read_parquet(r"D:\Xelp_work\FSL Project\Sprint_2\HCFA_Results\Ground_truth_from_Json.parquet")
Extraction_data = pd.read_parquet(r"D:\Xelp_work\FSL Project\Sprint_2\HCFA_Results\HCFA_Validation_data_results.parquet")

In [95]:
master_df.columns, Extraction_data.columns

(Index(['FileName', 'KeyName', 'Value'], dtype='object'),
 Index(['Field_Name', 'Value', 'Image_Name'], dtype='object'))

In [96]:
Extraction_data.rename(columns={'Image_Name': 'FileName'}, inplace=True)
# Rename Field_Name to KeyName in Extraction_data to match master_df
Extraction_data.rename(columns={'Field_Name': 'KeyName'}, inplace=True)
# Rename Value columns for clarity
Extraction_data.rename(columns={'Value': 'XELP_Output'}, inplace=True)
master_df.rename(columns={'Value': 'Ground_truth'}, inplace=True) 

In [113]:
master_df.shape, Extraction_data.shape

((1268666, 3), (1264044, 3))

In [97]:
master_df.columns, Extraction_data.columns

(Index(['FileName', 'KeyName', 'Ground_truth'], dtype='object'),
 Index(['KeyName', 'XELP_Output', 'FileName'], dtype='object'))

In [165]:
gc.collect()

0

In [186]:
import pandas as pd
from tqdm import tqdm

# Initialize an empty DataFrame to store the merged results
Merged_data_frame_all_images = pd.DataFrame()
gc.collect()
# Iterate over each group of images in the master DataFrame
for img_name, grp_b_im in tqdm(master_df.groupby('FileName')):
    # Handle duplicates in the master DataFrame
    counts_master = grp_b_im['KeyName'].value_counts()
    mask_master = grp_b_im['KeyName'].map(counts_master) > 1
    grp_b_im.loc[mask_master, 'KeyName'] = grp_b_im['KeyName'] + (grp_b_im.groupby('KeyName').cumcount() + 1).astype(str)
    
    # Filter and handle duplicates in the extraction DataFrame
    extraction_for_img = Extraction_data[Extraction_data["FileName"] == img_name]
    counts_extraction = extraction_for_img['KeyName'].value_counts()
    mask_extraction = extraction_for_img['KeyName'].map(counts_extraction) > 1
    extraction_for_img.loc[mask_extraction, 'KeyName'] = extraction_for_img['KeyName'] + (extraction_for_img.groupby('KeyName').cumcount() + 1).astype(str)
    
    # Merge the processed groups
    each_image_merged = pd.merge(grp_b_im, extraction_for_img, on=['FileName','KeyName'], how='outer')
    
    # Concatenate the merged data to the final DataFrame
    Merged_data_frame_all_images = pd.concat([Merged_data_frame_all_images, each_image_merged], ignore_index=True)

# Display the final merged DataFrame
Merged_data_frame_all_images.fillna('[BLANK]', inplace=True)
Merged_data_frame_all_images["XELP_Output"] = Merged_data_frame_all_images["XELP_Output"].str.replace("<one>", "1", regex=False)

100%|██████████████████████████████████████████████████████████████████████████████| 6981/6981 [08:14<00:00, 14.13it/s]


FileName            KeyName          Ground_truth  \
0        BSC134A9O003_000_HCFA.tiff  1A_PriInsIDNumber          R6J588215755   
1        BSC134A9O003_000_HCFA.tiff      2_PatFullName       SUMANTRI, TEGUH   
2        BSC134A9O003_000_HCFA.tiff           3_PatDOB              10151973   
3        BSC134A9O003_000_HCFA.tiff         5_PatAddr1  14360 VOSE ST APT219   
4        BSC134A9O003_000_HCFA.tiff          5_PatCity              VAN NUYS   
...                             ...                ...                   ...   
1270014  PHP8843RO035_000_HCFA.tiff     24_AnesEndTime               [BLANK]   
1270015  PHP8843RO035_000_HCFA.tiff   24_AnesTotalTime               [BLANK]   
1270016  PHP8843RO035_000_HCFA.tiff    24_AnesTotalMin               [BLANK]   
1270017  PHP8843RO035_000_HCFA.tiff         24_AnesMod               [BLANK]   
1270018  PHP8843RO035_000_HCFA.tiff       24_AnesUnits               [BLANK]   

                  XELP_Output  
0                R6J588215755  
1             SUMANTRI, TEGUH  
2                    10151973  
3        14360 VOSE ST APT219  
4                    VAN NUYS  
...                       ...  
1270014               [BLANK]  
1270015               [BLANK]  
1270016               [BLANK]  
1270017               [BLANK]  
1270018               [BLANK]  

[1270019 rows x 4 columns]

In [187]:
Merged_data_frame_all_images.shape

(1270019, 4)

In [188]:
Merged_data_frame_all_images.drop_duplicates()

FileName            KeyName          Ground_truth  \
0        BSC134A9O003_000_HCFA.tiff  1A_PriInsIDNumber          R6J588215755   
1        BSC134A9O003_000_HCFA.tiff      2_PatFullName       SUMANTRI, TEGUH   
2        BSC134A9O003_000_HCFA.tiff           3_PatDOB              10151973   
3        BSC134A9O003_000_HCFA.tiff         5_PatAddr1  14360 VOSE ST APT219   
4        BSC134A9O003_000_HCFA.tiff          5_PatCity              VAN NUYS   
...                             ...                ...                   ...   
1270014  PHP8843RO035_000_HCFA.tiff     24_AnesEndTime               [BLANK]   
1270015  PHP8843RO035_000_HCFA.tiff   24_AnesTotalTime               [BLANK]   
1270016  PHP8843RO035_000_HCFA.tiff    24_AnesTotalMin               [BLANK]   
1270017  PHP8843RO035_000_HCFA.tiff         24_AnesMod               [BLANK]   
1270018  PHP8843RO035_000_HCFA.tiff       24_AnesUnits               [BLANK]   

                  XELP_Output  
0                R6J588215755  
1             SUMANTRI, TEGUH  
2                    10151973  
3        14360 VOSE ST APT219  
4                    VAN NUYS  
...                       ...  
1270014               [BLANK]  
1270015               [BLANK]  
1270016               [BLANK]  
1270017               [BLANK]  
1270018               [BLANK]  

[1270019 rows x 4 columns]

In [189]:
error_images = ["BSC7N4NDO024_000_HCFA.tiff", "BSC3844JO030_000_HCFA.tiff", "BSC854FEO028_000_HCFA.tiff", "BSC85433O001_000_HCFA.tiff", "BSC7T6TRO002_000_HCFA.tiff"]

In [190]:
Merged_data_frame_all_images = Merged_data_frame_all_images[~Merged_data_frame_all_images['FileName'].isin(error_images)]

In [191]:
def strip_whitespace(x):
    if isinstance(x, str):  # Check if the value is a string
        return x.strip()
    return x

In [192]:
Merged_data_frame_all_images = Merged_data_frame_all_images.applymap(strip_whitespace)

In [204]:
tqdm.pandas()

# Apply the lambda function with progress tracking to add the 'Matching' column
Merged_data_frame_all_images['Matching'] = Merged_data_frame_all_images.progress_apply(
    lambda x: 1 if str(x['Ground_truth']).strip() == str(x['XELP_Output']).strip() else 0,
    axis=1
)

100%|████████████████████████████████████████████████████████████████████| 1268992/1268992 [00:07<00:00, 167852.61it/s]


In [233]:
Merged_data_frame_all_images.to_parquet("HCFA_Validation_split_evaluation.parquet", index=False)

In [209]:
Merged_data_frame_all_images_wo_blank = Merged_data_frame_all_images[Merged_data_frame_all_images["XELP_Output"] != '[BLANK]']

In [212]:
Merged_data_frame_all_images_wo_blank

FileName                 KeyName  \
0        BSC134A9O003_000_HCFA.tiff       1A_PriInsIDNumber   
1        BSC134A9O003_000_HCFA.tiff           2_PatFullName   
2        BSC134A9O003_000_HCFA.tiff                3_PatDOB   
3        BSC134A9O003_000_HCFA.tiff              5_PatAddr1   
4        BSC134A9O003_000_HCFA.tiff               5_PatCity   
...                             ...                     ...   
1269996  PHP8843RO035_000_HCFA.tiff    10A_PatConditionEmpN   
1269998  PHP8843RO035_000_HCFA.tiff   10B_PatConditionAutoN   
1270000  PHP8843RO035_000_HCFA.tiff  10C_PatConditionOtherN   
1270010  PHP8843RO035_000_HCFA.tiff          25_BillProvEIN   
1270011  PHP8843RO035_000_HCFA.tiff    27_AcceptAssignmentY   

                 Ground_truth           XELP_Output  Matching  
0                R6J588215755          R6J588215755         1  
1             SUMANTRI, TEGUH       SUMANTRI, TEGUH         1  
2                    10151973              10151973         1  
3        14360 VOSE ST APT219  14360 VOSE ST APT219         1  
4                    VAN NUYS              VAN NUYS         1  
...                       ...                   ...       ...  
1269996                     X                     X         1  
1269998                     X                     X         1  
1270000                     X                     X         1  
1270010                     X                     X         1  
1270011                     X                     X         1  

[443019 rows x 5 columns]

In [210]:
Merged_data_frame_all_images_wo_blank['Matching'].value_counts(normalize=True)

Matching
1    0.975811
0    0.024189
Name: proportion, dtype: float64

In [216]:
Merged_data_frame_all_images_wo_blank[Merged_data_frame_all_images_wo_blank['Matching'] == 1]['KeyName'].value_counts()

KeyName
33_BillProvState        6940
5_PatState              6927
3_PatDOB                6875
25_BillProvFedIdCode    6871
33_BillProvCity         6863
                        ... 
24_NDCUnitsQual6           7
24_NDC5                    6
10A_PatConditionEmpY       6
24_NDC6                    3
24_AnesStartTime2          1
Name: count, Length: 202, dtype: int64

In [226]:
Merged_data_frame_all_images["XELP_Output"] = Merged_data_frame_all_images["XELP_Output"].str.replace("<one>", "1", regex=False)

In [230]:

Merged_data_frame_all_images[(Merged_data_frame_all_images['XELP_Output'] != '[BLANK]')&(Merged_data_frame_all_images['KeyName'] == '24_AnesStartTime') & (Merged_data_frame_all_images['Matching'] == 0)][:60]


Empty DataFrame
Columns: [FileName, KeyName, Ground_truth, XELP_Output, Matching]
Index: []

In [177]:
blank_keys = ["20_OSLabCharges", "11D_PriInsOtherPlanY", "19_LocalUse", '17_RefProvOrgName',
 '30_BalanceDue',
 '24_NDCCharges',
 '24_NDCQualifier',
 '7_PriInsPhoneNumber','32_AmbToFacProvPostCodeExt',
 '20_OSLabY',
 '31_RenProvTaxonomyCode',
 '24C_EMG',
 '11D_PriInsOtherPlanN',
 '5_PatPhoneNumber',
 '20_OSLabN',
 '22_MedicaidCode',
 '29_AmountPaid',
 '33_BillProvPhone',
 '16_PatUTWToDate',
 '22_MedicaidRefNum',
 '24_AnesMod']

In [182]:
dummy = Merged_data_frame_all_images[Merged_data_frame_all_images['KeyName'].isin(blank_keys)]

In [183]:
dummy

FileName               KeyName Ground_truth  \
7        BSC134A9O003_000_HCFA.tiff      5_PatPhoneNumber      [BLANK]   
13       BSC134A9O003_000_HCFA.tiff   7_PriInsPhoneNumber      [BLANK]   
33       BSC134A9O003_000_HCFA.tiff       16_PatUTWToDate      [BLANK]   
38       BSC134A9O003_000_HCFA.tiff     17_RefProvOrgName      [BLANK]   
42       BSC134A9O003_000_HCFA.tiff       20_OSLabCharges      [BLANK]   
...                             ...                   ...          ...   
1270004  PHP8843RO035_000_HCFA.tiff  11D_PriInsOtherPlanN      [BLANK]   
1270005  PHP8843RO035_000_HCFA.tiff           19_LocalUse      [BLANK]   
1270007  PHP8843RO035_000_HCFA.tiff             20_OSLabY      [BLANK]   
1270008  PHP8843RO035_000_HCFA.tiff             20_OSLabN      [BLANK]   
1270017  PHP8843RO035_000_HCFA.tiff            24_AnesMod      [BLANK]   

        XELP_Output  Matching  
7           [BLANK]         1  
13          [BLANK]         1  
33          [BLANK]         1  
38          [BLANK]         1  
42          [BLANK]         1  
...             ...       ...  
1270004     [BLANK]         1  
1270005     [BLANK]         1  
1270007     [BLANK]         1  
1270008     [BLANK]         1  
1270017     [BLANK]         1  

[136532 rows x 5 columns]

In [184]:
Merged_data_frame_all_images[Merged_data_frame_all_images['Matching'] == 0]['KeyName'].value_counts()[:60]

KeyName
32_FacProvOrgName         1044
31_PrnRenProvFullName      815
26_PatAcctNo               612
33_BillProvOrgName         608
33_BillProvAddr1           544
32_FacProvAddr1            520
32_FacProvFullName         465
31_RenDateSigned           359
2_PatFullName              347
4_PriInsFullName           327
33_BillProvFullName        303
1A_PriInsIDNumber          282
13_PriSignonFileList       256
32_FacProvPostCode         253
33_BillProvPostCode        239
17_RefProvFullName         214
33_BillProvNPIId           206
7_PriInsAddr1              180
5_PatAddr1                 177
11_PriInsPolGrpNumber      167
12_PatSignonFile           155
9_SecInsFullName           143
11C_PriInsPlanName         142
28_TotalCharges            141
32_FacProvCity             125
32_FacProvNPIId            116
21_DiagCode2               108
33_BillProvCity            108
25_BillProvEIN             108
25_BillProvFedIdCode       104
24J_RenProvNPIId            97
21_DiagCode1                93
